In [1]:
import os
import math
import random
import numpy as np
import pandas as pd
import torch
from torch import nn
from torch import utils
from mdl import torch as mdl

In [2]:
train_df = pd.read_csv('/home/data/taobao/tb_data_train.csv')
test_df = pd.read_csv('/home/data/taobao/tb_data_test.csv')
train_df

uid     iid   cid  pv  fav  cart  buy          ts  ulen      neg  \
0              0       0     0   1    0     0    0  1511544070     0   553991   
1              0       1     1   1    0     0    0  1511561733     1  2096907   
2              0       2     2   1    0     0    0  1511572885     2  3290336   
3              0       3     3   1    0     0    0  1511593493     3   261027   
4              0       4     0   1    0     0    0  1511596146     4  2638749   
...          ...     ...   ...  ..  ...   ...  ...         ...   ...      ...   
74983975  987993    7894   964   1    0     0    0  1512293252    36  2857250   
74983976  987993  635418  2360   1    0     0    0  1512293282    37  2891616   
74983977  987993  655781  2360   1    0     0    0  1512293403    38  1884042   
74983978  987993  638297   706   1    0     0    0  1512293792    39   358038   
74983979  987993   78548   706   1    0     0    0  1512293827    40  3054020   

          negc  
0           11  
1          671  
2         1482  
3          619  
4          317  
...        ...  
74983975  6201  
74983976   166  
74983977   449  
74983978   284  
74983979   920  

[74983980 rows x 11 columns]

In [3]:
import random
class TaobaoData(mdl.DataModule):
    def __init__(self, batch_size=32, L=5):
        super().__init__()
        self.save_hyperparameters()
        self.train_df = train_df
        self.test_df = test_df
        self.uid_count = 987994
        self.iid_count = 4162024
        self.cid_count = 9439
        self.uid_nps = [self.train_df.uid.to_numpy(), self.test_df.uid.to_numpy()]
        self.iid_nps = [self.train_df.iid.to_numpy(), self.test_df.iid.to_numpy()]
        self.cid_nps = [self.train_df.cid.to_numpy(), self.test_df.cid.to_numpy()]
        self.act_nps = [self.train_df.loc[:, ['pv','fav','cart','buy']].to_numpy(), 
                       self.test_df.loc[:, ['pv','fav','cart','buy']].to_numpy()]
        self.ts_nps = [self.train_df.ts.to_numpy(), self.test_df.ts.to_numpy()]
        self.neg_nps = [self.train_df.neg.to_numpy(), self.test_df.neg.to_numpy()]
        self.negc_nps = [self.train_df.negc.to_numpy(), self.test_df.negc.to_numpy()]
        self.train_ulen_np = self.train_df.ulen.to_numpy()
        self.test_tpos_np = self.test_df.tpos.to_numpy()
        self.train_ds = TaobaoData.Dataset(self, True)
        self.test_ds = TaobaoData.Dataset(self, False)
    def get_dataloader(self, train=True):
        return torch.utils.data.DataLoader(self.train_ds if train else self.test_ds, batch_size=self.batch_size, shuffle=True)
    class Dataset:
        def __init__(self, data, is_train=True):
            self.data = data
            self.is_train = is_train
            self.df = self.data.train_df if self.is_train else self.data.test_df 
            self.total_len = len(self.df)
            self.npi = 0 if self.is_train else 1
            self.retry_count = 0
            self.total_get_count = 0
        def __len__(self):
            return len(self.df)
        def __getitem__(self, idx):
            if self.is_train:
                self.total_get_count += 1
                while self.data.train_ulen_np[idx] < self.data.L:
                    idx = random.randint(0, self.total_len-1)
                    self.retry_count += 1
                    # if self.retry_count % 1024 == 0:
                    #     print(f'retry {self.retry_count} times, total get {self.total_get_count} times')
                seq = idx - self.data.L
            else:
                seq = self.data.test_tpos_np[idx] - self.data.L
            assert self.data.uid_nps[0][seq] == self.data.uid_nps[self.npi][idx]
            ts = self.data.ts_nps[self.npi][idx]
            return (self.data.uid_nps[self.npi][idx],  # uid
                    self.data.iid_nps[0][seq:seq+self.data.L],  # iid history seq
                    self.data.cid_nps[0][seq:seq+self.data.L],  # cid history seq
                    self.data.act_nps[0][seq:seq+self.data.L],  # act history seq
                    ts - self.data.ts_nps[0][seq:seq+self.data.L],  # ts history seq
                    self.data.iid_nps[self.npi][idx],  # iid target
                    self.data.cid_nps[self.npi][idx],  # cid target
                    self.data.act_nps[self.npi][idx],  # act target
                    self.data.neg_nps[self.npi][idx],  # iid neg target
                    self.data.negc_nps[self.npi][idx])  # cid neg target
data = TaobaoData(batch_size=128)
# train_loader = torch.utils.data.DataLoader(data.train_ds, batch_size=2)
# test_loader = torch.utils.data.DataLoader(data.test_ds, batch_size=2)
train_loader = data.train_dataloader()
test_loader = data.val_dataloader()
len(test_loader)
# next(iter(train_loader)), next(iter(test_loader))

7679

In [4]:
class Lable10Classifier(mdl.Module):
    def __init__(self, lr=0.001, pos_weight=0.5):
        super().__init__(plot_train_per_epoch=100, plot_valid_per_epoch=50)
        self.save_hyperparameters()
    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=self.lr)
    def loss(self, Y_hat, y, averaged=True):
        return nn.functional.binary_cross_entropy(
            Y_hat, y.broadcast_to(Y_hat.shape), reduction='mean' if averaged else 'none')
    def accuracy(self, Y_hat, y, averaged=True):
        if y == 1:
            compare = (Y_hat >= 0.5).float()
        else:
            compare = (Y_hat < 0.5).float()
        return mdl.reduce_mean(compare) if averaged else compare
    def training_step(self, batch):
        y1, y2 = self(*batch)
        l1, l2 = self.loss(y1, torch.tensor(1.0, device=y1.device)), self.loss(y2, torch.tensor(0.0, device=y2.device))
        l = l1 * self.pos_weight + l2 * (1 - self.pos_weight)
        self.plot('loss', l, train=True)
        return l
    def validation_step(self, batch):
        y1, y2 = self(*batch)
        l1, l2 = self.loss(y1, torch.tensor(1.0, device=y1.device)), self.loss(y2, torch.tensor(0.0, device=y2.device))
        a1, a2 = self.accuracy(y1, 1), self.accuracy(y2, 0)
        l = l1 * self.pos_weight + l2 * (1 - self.pos_weight)
        a = a1 * self.pos_weight + a2 * (1 - self.pos_weight)
        self.plot('loss', l, train=False)
        # self.plot('acc', a, train=False)
        self.plot('acc1', a1, train=False)
        self.plot('acc2', a2, train=False)

class TaobaoAttentionSeqReco(Lable10Classifier):
    def __init__(self, dropout=0.2):
        super().__init__()
        self.save_hyperparameters()
        self.hidden_dim = 32
        self.user_embed = nn.Embedding(data.uid_count, self.hidden_dim)
        self.item_embed = nn.Embedding(data.iid_count, self.hidden_dim)
        self.icls_embed = nn.Embedding(data.cid_count, self.hidden_dim)
        self.acts_embed = nn.Linear(4, self.hidden_dim, bias=False)
        nn.init.normal_(self.acts_embed.weight)
        self.pos_enc = mdl.PositionalEncoding(self.hidden_dim * 2, self.dropout, 100, reverse=True, shift=1)
        self.attention = nn.MultiheadAttention(self.hidden_dim * 2, 4, vdim=self.hidden_dim * 3, batch_first=True, dropout=self.dropout)
        # self.addnorm = mdl.AddNorm(self.hidden_dim, self.dropout)
        self.att_norm = nn.Sequential(nn.Dropout(self.dropout), nn.LayerNorm(self.hidden_dim * 2))
        self.mlp = nn.Sequential(
            nn.Linear(self.hidden_dim * 5, self.hidden_dim * 2),
            nn.LeakyReLU(), nn.Dropout(self.dropout), 
            nn.Linear(self.hidden_dim * 2, self.hidden_dim),
            nn.LeakyReLU(), nn.Dropout(self.dropout), 
            nn.Linear(self.hidden_dim, 1))
        self.mlp.apply(lambda mod: nn.init.kaiming_normal_(mod.weight) if isinstance(mod, nn.Linear) else None)
        self.target_pos_enc = self.pos_enc.get_enc(0).to(torch.device('cuda:0'))
    def forward(self, uid, iid_seq, cid_seq, act_seq, ts_seq, iid, cid, act, iid_neg, cid_neg):
        user_e = self.user_embed(uid)
        iid_seq_e = self.pos_enc(torch.cat((self.item_embed(iid_seq), self.icls_embed(cid_seq)), dim=2))
        ica_seq_e = torch.cat((iid_seq_e, self.acts_embed(act_seq.float())), dim=2)
        target_e = torch.cat((self.item_embed(iid), self.icls_embed(cid)), dim=1) + self.target_pos_enc
        target_neg_e = torch.cat((self.item_embed(iid_neg), self.icls_embed(cid_neg)), dim=1) + self.target_pos_enc
        return self.network(user_e, iid_seq_e, ica_seq_e, target_e), self.network(user_e, iid_seq_e, ica_seq_e, target_neg_e)
    def network(self, user_e, seq_k_e, seq_v_e, target_e):
        long_interest_e = self.attention(target_e.unsqueeze(1), seq_k_e, seq_v_e)[0].squeeze(1)
        input_e = torch.cat((self.att_norm(long_interest_e), user_e, target_e), dim=1)
        output = self.mlp(input_e).squeeze()
        return nn.functional.sigmoid(output)
model = TaobaoAttentionSeqReco()
mdl.Trainer(max_epochs=5, num_gpus=1).fit(model, data) 

KeyboardInterrupt: 

In [16]:
# model.user_embed.weight.grad.sum()
# model.item_embed.weight.grad.sum()
# model.mlp[6].weight.grad
# torch.save(model.state_dict(), '/home/data/taobao/model/taobao_reco.pth')

sum(p.numel() for p in model.parameters())



165133985

In [6]:
with torch.inference_mode():
    model.eval()
    b = next(iter(train_loader))
    y = model(*[d.to(torch.device('cuda:0')) for d in b])
y


(tensor([0.9963, 0.6729, 0.9979, 0.9972, 0.9992, 0.7878, 0.9959, 0.8780, 0.9986,
         0.8851, 0.9990, 0.9945, 0.4520, 0.9890, 0.9990, 0.7167, 0.9436, 0.8665,
         0.9984, 0.3908, 0.7184, 0.9976, 0.9413, 0.9937, 0.9911, 0.1060, 0.9931,
         0.9983, 0.9860, 0.9900, 0.9913, 0.9949, 0.9924, 0.9924, 0.9983, 0.9903,
         0.9982, 0.9931, 0.9932, 0.9251, 0.9970, 0.8525, 0.9988, 0.9982, 0.9986,
         0.2549, 0.9991, 0.0728, 0.9981, 0.9983, 0.9770, 0.9940, 0.9364, 0.9977,
         0.9770, 0.4569, 0.9231, 0.9734, 0.7689, 0.2600, 0.7459, 0.9857, 0.8258,
         0.9916, 0.9702, 0.9881, 0.9994, 0.9210, 0.2296, 0.9984, 0.9986, 0.9776,
         0.9248, 0.9991, 0.5447, 0.9920, 0.9774, 0.9938, 0.9991, 0.9994, 0.9957,
         0.9995, 0.9976, 0.8730, 0.6634, 0.9938, 0.5704, 0.4048, 0.9955, 0.8936,
         0.9923, 0.9952, 0.9773, 0.5190, 0.9978, 0.9987, 0.9956, 0.9974, 0.9991,
         0.9993, 0.9990, 0.9921, 0.9920, 0.9992, 0.9994, 0.9711, 0.9957, 0.9997,
         0.6503, 0.9807, 0.8

In [97]:
tt=torch.tensor([1,2,3], device='cuda:0')
tt[2]

tensor(3, device='cuda:0')